# Load Libraries

In [ ]:
%load_ext autoreload
%autoreload 2
%reload_ext autoreload

import os
os.chdir("/home/dalai/GNN_E")
print(os.getcwd())

from scripts.models import *
import pandas as pd
from scripts.utils import *
from math import ceil
import gc
from types import SimpleNamespace
from pathlib import Path


import torch
import torch.optim as optim

print(torch.cuda.is_available())
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)
print(torch.__version__)

/home/dalai/GNN_E


/home/dalai/.conda/envs/gat_gpu/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


True
cuda
1.13.1+cu116


# Hyperparamters

In [11]:
# from VIB param_parser.py
args = SimpleNamespace(
    ### General par
    num_classes = 13, # based on df_movie choosen
    type_labels = "single", # single, thr_$value, regression
    batch_size = 32,
    test_batch_size = 32,
    percentage_train = 0.8,
    percentage_val = 0.0,
    test_train_splitting_mode = "Vertical", # Vertical, Horizontal
    window_half_size = 4,
    node_feat = "symmetricwindow", #how to create the feat of each node
    intial_adj_method = "clique", #how to initiliaze graph connectivity (node attr)
    FN = "Lymbic", #Functional networj in case we want to use a subset of nodes
    ### VIB par
    dataset_name="EMOTION", #"IMDB-BINARY",
    backbone="GCN",
    graph_type="prob",
    graph_metric_type="mlp",
    repar=True,
    num_layers=2,
    hidden_dim=16,
    folds=10,
    epochs=10,
    lr=0.0001, #ATTENTION: changed from 0.001
    lr_decay_factor=0.5,
    lr_decay_step_size=50,
    weight_decay=5e-5,
    beta=0.00001, #ATTNETION: not use kl loss#0.00001,
    IB_size=16,
    num_per=16,
    feature_denoise=False,
    top_k=10,
    epsilon=0.3,
    graph_skip_conn=0.0,
    graph_include_self=True
)

# Load df all Movies

In [ ]:
# Load all movies with labels csv
df_all_movies = pd.read_csv(f"data/processed/all_movies_labelled_{args.num_classes}_{args.type_labels}.csv")

32


In [ ]:
############
#JUST FOR PROVA: select subset of movies
#df_all_movies = df_all_movies[df_all_movies.movie.isin([0,3])]
############

# Split in Train, Validation, Test

In [ ]:
print(f"Splitting {args.test_train_splitting_mode}...")

if args.test_train_splitting_mode == "Vertical":
    df_train, df_test = split_train_test_vertically(
        df_all_movies, 
        test_movies_dict = {"BigBuckBunny": 2, "FirstBite": 4, "Superhero": 9}
    )
    df_val = df_train[df_train.id == 99] #make sure to be empty
elif args.test_train_splitting_mode == "Horizontal":
    df_train, df_val, df_test = split_train_val_test_horizontally(
        df_all_movies, 
        percentage_train=args.percentage_train, 
        percentage_val=args.percentage_val, #0 to not have nay val set
        path_pickle_delay="data/raw/labels/run_onsets.pkl",
        path_movie_title_mapping="data/raw/labels/category_mapping_movies.csv", 
        tr_len=1.3
    )
elif args.test_train_splitting_mode == "MovieRest":
    df_rest = pd.read_csv("data/raw/rest/Rest_compiled414_processed.csv")
    df_train, df_test = split_train_test_rest_classification(df_all_movies, df_rest)
    df_val = df_train[df_train.id == 99] #make sure to be empty

Splitting Vertical


# Create dataset (i.e. graph list)

In [5]:
dataset_train = DatasetEmo(
    df = df_train, #df with mvoies to use
    node_feat = args.node_feat, #"singlefmri", "symmetricwindow", "pastwindow"
    intial_adj_method = args.intial_adj_method,
        # "clique"
        #FC dynamic:  "fcmovie", "fcwindow"
        #FN (subcorticla with clique): "FN_const" "FN_edgeAttr_FC_window" "FN_edgeAttr_FC_movie"
    FN = args.FN, #['Vis' 'SomMot' 'DorsAttn' 'SalVentAttn' 'Limbic' 'Cont' 'Default' 'Sub']
    FN_paths = "data/raw/FN_raw",
    sizewind = args.window_half_sizes
)

dataset_val = DatasetEmo(
    df = df_val,
    node_feat = args.node_feat,
    intial_adj_method = args.intial_adj_method,
    FN = args.FN,
    FN_paths = "data/raw/FN_raw",
    sizewind = args.window_half_sizes
)

dataset_test = DatasetEmo(
    df = df_test,
    node_feat = args.node_feat,
    intial_adj_method = args.intial_adj_method,
    FN = args.FN,
    FN_paths = "data/raw/FN_raw",
    sizewind = args.window_half_sizes
)

# Extarct the list of graphs of each dataset
graphs_list_train = dataset_train.get_graphs_list()
graphs_list_val = dataset_val.get_graphs_list()
graphs_list_test = dataset_test.get_graphs_list()

print(f"Number Batces Train {len(graphs_list_train)/args.batch_size}")
print(f"Number Batces Val {len(graphs_list_val)/args.batch_size}")
print(f"Number Batces Test {len(graphs_list_test)/args.batch_size}")


Movies in this df: [ 0  1  3  5  6  7  8 10 11 12 13]
Creating the graph 0 1 0/382
Creating the graph 0 1 1/382
Creating the graph 0 1 2/382
Creating the graph 0 1 3/382
Creating the graph 0 1 4/382
Creating the graph 0 1 5/382
Creating the graph 0 1 6/382
Creating the graph 0 1 7/382
Creating the graph 0 1 8/382
Creating the graph 0 1 9/382
Creating the graph 0 1 10/382
Creating the graph 0 1 11/382
Creating the graph 0 1 12/382
Creating the graph 0 1 13/382
Creating the graph 0 1 14/382
Creating the graph 0 1 15/382
Creating the graph 0 1 16/382
Creating the graph 0 1 17/382
Creating the graph 0 1 18/382
Creating the graph 0 1 19/382
Creating the graph 0 1 20/382
Creating the graph 0 1 21/382
Creating the graph 0 1 22/382
Creating the graph 0 1 23/382
Creating the graph 0 1 24/382
Creating the graph 0 1 25/382
Creating the graph 0 1 26/382
Creating the graph 0 1 27/382
Creating the graph 0 1 28/382
Creating the graph 0 1 29/382
Creating the graph 0 1 30/382
Creating the graph 0 1 31/

# Istantiate the Model

In [12]:
# following VIB main.py
import VIB.gsl as gsl

# Number fo features for each node
num_node_features = graphs_list_train[0].x.shape[1]
print("\nnum_node_features : %d, num_classes : %d"%(num_node_features, args.num_classes))

model = gsl.VIBGSL(
            args, 
            num_node_features, 
            args.num_classes)
print(model.__repr__())


num_node_features : 9, num_classes : 13
[ Graph Learner metric type: mlp, Graph Type: prob ]


VIBGSL


# Train

In [ ]:
from VIB.train_eval import *

# Useful if the code get some strange anomaly
torch.autograd.set_detect_anomaly(True)

train_losses, train_accs, test_losses, test_accs = my_train_and_evaluate(
    train_graphs_list = graphs_list_train,
    test_graphs_list = graphs_list_test,
    model = model,
    epochs = args.epochs, 
    batch_size = args.batch_size, 
    test_batch_size = args.test_batch_size,
    lr = args.lr, 
    lr_decay_factor = args.lr_decay_factor, 
    lr_decay_step_size = args.lr_decay_step_size,
    weight_decay = args.weight_decay, 
)

# Evaluate on test
Wite the last epoch model.

In [ ]:
# Extarct accuracy, learnt grpahs and predicted lablled in test set
acc_test, new_graphs_list_test, pred_y_test = my_interpretation(
        graphs_list = graphs_list_test,
        model_trained = model,
        batch_size = args.batch_size,
)

# Extarct ground.truth labels
y_test = [g.y for g in graphs_list_test]

# Builf adj matrices of leant graphs
new_graphs_list_test_adj = {}
for g in new_graphs_list_test:
    adj = to_dense_adj(edge_index=g.edge_index, edge_attr=g.edge_attr)
    adj = adj.cpu().squeeze().numpy()
    new_graphs_list_test_adj.update({g.y: adj})

# Save Results

In [ ]:
RESULT_DIR = Path(f"data/results/VIB/{acc_test:.2f}")
os.makedirs(RESULT_DIR, exist_ok=True)

# Convert SimpleNamespace to dictionary
results_dict = vars(args)
# Create dict with all results
results_dict.update(
    {
        "train_losses": train_losses,
        "train_accs": train_accs,
        "test_losses": test_losses,
        "test_accs": test_accs, 
        "acc_test": acc_test,
        "pred_y_test": pred_y_test, 
        "y_test": y_test,
        "new_graphs_list_test_adj": new_graphs_list_test_adj
    }
)
with open(os.path.join(RESULT_DIR, 'results.json', 'w')) as f:
    json.dump(results_dict, f, indent=4)


# Save the entire model (architecture + weights)
torch.save(model, os.path.join(RESULT_DIR, 'full_model.pth'))


# For future Loading
#model = torch.load('full_model.pth')
#model = model.to(torch.device('cuda' if torch.cuda.is_available() else 'cpu'))


# Interpretation

In [ ]:
graphs_list_test_fear = [g for g in graphs_list_test if g.y == 5]
print(len(graphs_list_test_fear))
print(graphs_list_test_fear[0])

In [ ]:
graphs_list, new_graphs_list, pred_y = my_interpretation(
        graphs_list = graphs_list_test_fear,
        model_trained = model,
        batch_size = args.batch_size,
)


In [ ]:
initial_graph = to_dense_adj(edge_index=graphs_list_test_fear[0].edge_index, edge_attr=graphs_list_test_fear[0].edge_attr)
new_graph = to_dense_adj(edge_index=new_graphs_list[0].edge_index, edge_attr=new_graphs_list[0].edge_attr)

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import torch

# Assuming initial_graph and new_graph are returned from to_dense_adj and are PyTorch tensors
# Move tensors to CPU and convert to numpy arrays
initial_graph_np = initial_graph.cpu().squeeze().numpy()  # Move to CPU, remove singleton dimensions, and convert to numpy
new_graph_np = new_graph.cpu().squeeze().numpy()  # Same for new_graph

# Set up the matplotlib figure
fig, ax = plt.subplots(1, 2, figsize=(12, 6))  # Create 2 subplots side by side

# Plot the initial graph adjacency matrix
sns.heatmap(initial_graph_np, cmap='Blues', ax=ax[0], square=True, cbar=True)
ax[0].set_title('Initial Graph Adjacency Matrix')
ax[0].set_xlabel('Nodes')
ax[0].set_ylabel('Nodes')

# Plot the new graph adjacency matrix
sns.heatmap(new_graph_np, cmap='Blues', ax=ax[1], square=True, cbar=True)
ax[1].set_title('New Graph Adjacency Matrix')
ax[1].set_xlabel('Nodes')
ax[1].set_ylabel('Nodes')

# Adjust layout
plt.tight_layout()
plt.show()


***
# ***

In [ ]:
#del model
gc.collect()
torch.cuda.empty_cache()
torch.cuda.reset_peak_memory_stats()
print(torch.cuda.memory_summary(device=None, abbreviated=False))